_Note: this document is also a Jupyter Notebook. You can download and run it from the [examples directory](https://ard.maxar.com/docs/sdk/examples/examples/) of the SDK documentation._

# ARD Orders

To run orders from Python the SDK has one main object: `Order` represents an order and its interaction with the API. 

In [ ]:
from max_ard import Order

The call signature for an `Order` includes the following keyword arguments:

- `acquisitions`: List of acquisition IDs to order.
- `select_id`: Order the results of a Select query with the Select ID. If ordering by select ID, do not include acquisition ID or an AOI in the order request. 
- `destination`: For S3 orders only, the destination of the tiles: an S3 bucket path like `s3://bucket/prefix`
- `output_config`: An output configuration dictionary, see `Output Configuration` below. Required if not using `destination`.
- `intersects`: Only generate tiles that intersect this WGS84 geometry. Accepts WKT or GeoJSON strings, most Python geospatial objects, or a file path to OGR-readable files
- `bbox`: Like `intersects`, but takes a bounding box list or tuple in the form `[XMIN YMIN XMAX YMAX]`
- `role_arn`: A trusted S3 Role ARN for the writer to assume so it can write tiles. This is not used if the s3 bucket policy is in place.
- `dry_run`: Boolean to dry-run the order. If `True`, submits the order for basic validation but will not generate tiles. Default is `False`.
- `bba` Boolean to use Bundle Block Adjustment to relatively align images within this order. Default is `False`.
- `metadata`: A dictionary of user-defined key-value pairs.


Orders can send notifications. Notifications are set up using these two
methods. Note: "dry run" orders do not send notifications since they do not start the order pipeline.

- `add_email_notification(address)`: add an email notification
- `add_sns_notification(topic)`: add an sns notification

### Output Configurations

ARD support delivering to Amazon S3, Google Cloud Storage, and Azure Blob Storage. You can configure the storage destination by passing a dictionary in the following formats:

#### Amazon S3

```python
{
    "amazon_s3": {
        "bucket": "my-ard-bucket"
        "prefix": "example/prefix"
    }
}
```

Note: you can also specify S3 locations using the parameter `destination="s3://bucket/prefix"` instead of `output_config`.


#### Azure Blob Storage

```python
{
    "azure_blob_storage": {
        "sas_url": "https://storagesample.blob.core.windows.net/?...",
        "container": "my-ard-container",
        "prefix": "example/prefix"
    }
}
```

#### Google Cloud Storage

```python
{
    "google_cloud_storage": {
        "service_credentials": <see note>,
        "bucket": "my-ard-bucket",
        "prefix": "example/prefix"
    }
}
```

`service_credentials` can accept two forms:

- a path to the service credentials JSON file. The SDK will read the file and convert it to Base64 encoding.
- a Base64-encoded string of the credentials file contents.


#### Storing Credentials for GCS and Azure

Output configurations for GCS and Azure can use a stored credential instead of the `service_credentials` or `sas_url` parameters. Use the parameter `"credentials_id"` instead. Secure credential storage is provided by the ARD API, see the [Credentials Service documentation](https://ard.maxar.com/docs/account_and_user_administration/credentials_service/) for more information and [Administration and Authentication](../authentication/) section for using the Python SDK to manage credentials.


```python
{
    "google_cloud_storage": {
        "credentials_id": "our-stored-credentials"
        "bucket": "my-ard-bucket",
        "prefix": "example/prefix"
    }
}
```
### Creating Orders

Create an order object with the desired parameters described above. Add notifications if needed. You can then call the `submit()` method to start the order processing.

In [ ]:
# an S3 order for a Select using `destination`
order = Order(destination='my_bucket/my_ard_tiles', select_id=<Select ID>)


In [ ]:
# a GCS order for acquisitions using `output_config` and a credentials file
output_config = {
    "google_cloud_storage": {
        "service_credentials": "path/to/credentials.json",
        "bucket": "my-ard-bucket",
        "prefix": "example/prefix"
    }
}

order = Order(output_config=output_config, acquisitions=['1030010052208D00'])

# add notifications if needed, then submit the order
order.add_email_notification('me@email.com')
order.submit()

### Properties of the Order object

An `Order` has the following properties after it is created:

- `request`: A container object storing the request options.

After the Order has been submitted with `submit()`, the following properties can be used:

- `order_id`: The order ID assigned to the request
- `finished`: Boolean if the order has finished running
- `status`: state of the order process: 'RUNNING', 'SUCCEEDED', or 'FAILED'

Once the Order has finished, this property is also available:

- `response`: A container object of the API response


### Methods of the Order object

`submit()`: submits the order

In [ ]:
order.submit()

# you can poll order.finished, but orders can take up to 3 days.

To create a `Order` object from ID, use the `from_id` classmethod:

In [ ]:
Order.from_id(id)

When an order is complete, you can use `ARDCollection` to work with the data, see the [Working with ARD Data]() section of the documentation.